# Test de création d'isochrones avec de nouvelles formes

On se base sur l'API de Navitia pour obtenir les points qui permettent de composer les isochrones.

Pour les besoins de ce tests, nous allons récupérer, à partir d'une requête sur un noeud d'origine, les noeuds et le temps nécessaire pour les atteindre avec les paramètres suivants:
* *durée maximale*: **30 minutes**
* *adresse de départ*: **"Châtelet - Les Halles, Place Basse, Quartier des Halles, Quartier Les Halles, Paris 1er Arrondissement, Paris, Île-de-France, France métropolitaine, 75001, France"**
* *date*: **2018-11-15** (*yyyy-mm-dd*)
* *heure*: **08:00**
* *API*: **Navitia** ([journeys](https://doc.navitia.io/#journeys))

## Explorer les requêtes et les premiers résultats
### Préparation
Tout d'abord, on importe le chemin du module dans le path

In [1]:
# Add module to path
import os
import sys

add_path = os.getcwd().replace('experiments', '')
sys.path.append(add_path)

### Utilisation de la librairie développée spécifiquement
Ensuite on lance le module avec les paramètres. Le temps de traitement peut être long car, pour les besoins du test, nous récupérons tous les plus courts chemins (*modes, stations, durées, ...*) du noeuds d'origine vers chaque noeud retourné par la requête initiale (*qui donne tous les noeuds permettant de créer un isochrone avec une durée maximale de X minutes*). 

In [2]:
from dotenv import load_dotenv
import docopt
import json
from pathlib import Path
from csv_to_json import csv_to_json
from isos_and_intersections import GetIso

param_csv = os.path.join(add_path, "params/test_journeys.csv")
param_json = os.path.join(add_path, "params/test_journeys.json")
places_cache = os.path.join(add_path, "params/places_cache.json")

#Parameters
env_path = Path(add_path) / '.env'
load_dotenv(dotenv_path=env_path)
TOKEN = os.getenv("NAVITIA_TOKEN")

columns_with_array_of_str = [
    "colors_iso",
    "addresses",
    "excluded_modes",
    "durations"
    ]

#JSON INPUT
json_file = csv_to_json(param_csv, param_json, ";", columns_with_array_of_str)

gdf_global = GetIso(param_json, places_cache, api="navitia", token=TOKEN).get_all_isos()

Ensuite on transforme les GeoDataframes obtenus en GeoJSON pour les lire et les cartographier plus facilement avec Bokeh. 

In [28]:
from geo_functions import gdf_to_geojson

#Filter: no "NR"
lines = gdf_global["journeys_details_lines"]
pts = gdf_global["journeys_details_pts"]
# filter_lines = lines.loc[lines["mode"] != "NR"]
# filter_pts = pts.loc[pts["mode"] != "NR"]

#Save to geojson
lines.to_file("lines_test.geojson", driver="GeoJSON")
pts.to_file("points_test.geojson", driver="GeoJSON")

#Transform gdf to geojson
columns_lines = list(lines.columns)
columns_pts = list(pts.columns)
geo_source_lines = gdf_to_geojson(lines, columns_lines, "epsg:3857")
geo_source_pts = gdf_to_geojson(pts, columns_pts, "epsg:3857")


### Exploration des résultats: cartographie de tous les chemins minimaux
On cartographie les lignes et les noeuds (*colorés en fonction du mode*) qui représentent tous les chemins minimaux entre le noeud d'origine et les X noeuds du réseau atteignables dans le temps donné. 

In [62]:
from bokeh.plotting import figure, show
from bokeh.io import output_notebook
from bokeh.tile_providers import STAMEN_TONER_BACKGROUND
from bokeh.models import GeoJSONDataSource, ColumnDataSource, CategoricalColorMapper
from bokeh.palettes import Colorblind8 as cb
from bokeh.transform import factor_cmap
import json

output_notebook()

# Set colors by mode
modes = ['Métro', 'RER', 'Bus', 'Tramway', 'NR']
palette = [cb[0], cb[1], cb[2], cb[4], 'grey']

color_mapper = CategoricalColorMapper(factors=modes, palette=palette)

# Set the tooltips for hover
TOOLTIPS = [
    ("index", "$index"),
    ("mode", "@mode"),
    ("name", "@name"),
    ("direction", "@direction")
]

p = figure(tooltips=TOOLTIPS)
p.width = 800
p.add_tile(STAMEN_TONER_BACKGROUND, alpha=0.2)


source_lines = GeoJSONDataSource(geojson=geo_source_lines)

p.multi_line(
    xs='xs',
    ys='ys',
    line_width=2,
    line_color= {'field': 'mode', 'transform': color_mapper},
    line_alpha=0.5,
    source=source_lines,
    legend="Lines"
)


source_pts = GeoJSONDataSource(geojson=geo_source_pts)
p.circle(
    x='x',
    y='y',
    size = 5,
    color = {'field': 'mode', 'transform': color_mapper},
    source=source_pts,
    legend="Nodes"
)

p.legend.click_policy="hide"

#Add a workaround to get a custom legend with geojson
#See https://github.com/bokeh/bokeh/issues/5904#issuecomment-296219499
for factor, color in zip(color_mapper.factors, color_mapper.palette):
    p.square(x=[], y=[], fill_color=color, size=10, line_alpha=0.0, legend=factor)

show(p)

Loading BokehJS ...

### Exploration des résultats: cartographie des durées et des distances à pied
On peut cartographier les noeuds du réseau issu de la requête principale:
* *avec la durée nécessaire pour les atteindre depuis le noeud d'origine*) => Carte "Duration from origin point"
* *avec le potiential de marche à pied depuis chaque noeud (en fonction du temps restant)*) => Carte "Walkable distance from nodes"

> Les 2 cartes sont liées (le pan et le zoom sont synchronisés sur les 2 cartes). 

In [87]:
from bokeh.palettes import Viridis256, Magma11, RdYlBu11, Greens9, Inferno256
from bokeh.plotting import figure, show
from bokeh.io import output_notebook
from bokeh.tile_providers import STAMEN_TONER_BACKGROUND
from bokeh.models import GeoJSONDataSource, ColumnDataSource, LinearColorMapper, LogTicker, ColorBar
from bokeh.layouts import gridplot
import json

from geo_functions import gdf_to_geojson

output_notebook()

TOOLTIPS = [
    ("name", "@to_name"),
    ("duration", "@duration"),
    ("walkable_distance", "@walkable_distance")
]

TOOLS = "pan,box_zoom,wheel_zoom,box_select,lasso_select,save,reset,hover"

#####################
#DURATION FROM ORIGIN
#####################
#Create color mapper
color_mapper = LinearColorMapper(palette=Viridis256)

#Prepare the data
columns_nodes = list(gdf_global["journeys_points"].columns)
test = gdf_global["journeys_points"].head(300)
nodes = gdf_to_geojson(gdf_global["journeys_points"], columns_nodes, "epsg:3857")

p = figure(
    title="Duration from origin point",
    tooltips=TOOLTIPS, 
    tools=TOOLS
)
p.width = 450
p.add_tile(STAMEN_TONER_BACKGROUND, alpha=0.2)

source_circles = GeoJSONDataSource(geojson=nodes)
p.circle(
    x='x',
    y='y',
    fill_color={'field': 'duration', 'transform': color_mapper},
    fill_alpha=0.5,
    line_color="white",
    line_alpha=0.0,
    size=10,
    source=source_circles
)

color_bar = ColorBar(color_mapper=color_mapper, ticker=LogTicker(),
                     label_standoff=120, border_line_color=None, location=(0,0))
p.add_layout(color_bar, 'right')
############################################

#####################
#WALKABLE DISTANCE
#####################
#Create color mapper
color_mapper = LinearColorMapper(palette=Viridis256)

p2 = figure(
    title="Walkable distance from nodes (meters)",
    x_range=p.x_range, 
    y_range=p.y_range,
    tooltips=TOOLTIPS,
    tools=TOOLS
)
p2.width = 450
p2.add_tile(STAMEN_TONER_BACKGROUND, alpha=0.2)

p2.circle(
    x='x',
    y='y',
    fill_color={'field': 'walkable_distance', 'transform': color_mapper},
    fill_alpha=0.5,
    line_color="white",
    line_alpha=0.0,
    size=10,
    source=source_circles
)

color_bar = ColorBar(color_mapper=color_mapper, ticker=LogTicker(),
                     label_standoff=120, border_line_color=None, location=(0,0))
p2.add_layout(color_bar, 'right')
############################################

grid = gridplot(
    [
        [p,p2]
    ],
    toolbar_location='right'
     )


show(grid)

Loading BokehJS ...

## Etude de variations de représentations
### Différentes manières de représenter les isochrones
#### Les buffers autour des stations et leur union

#### Les isochrones pédestres en fonction du réseau viaire autour des stations et leur union

#### Simplifications d'isochrones et propositions de représentations